In [ ]:
import matplotlib.pyplot as plt
import numpy as np

In [ ]:
plt.rcParams['animation.ffmpeg_path']=r'C:\ffmpeg\bin\ffmpeg.exe'

In [ ]:
dzmax_bos = 0.23458739
dzmax_SF = 1.40881546
t_final = 100 #years 
dt = 1
dz1 = 3.75
dz2 = 6

Cv_SF = 1 #m^2/year
Cv_bos = 12 #m^2/year
b_SF = Cv_SF*(dt/dz1**2)
b_bos = Cv_bos*(dt/dz2**2) 
b = np.array([b_SF,b_bos])

#print(b_SF, b_bos) #must be less than 0.5
print(b)

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='consol', artist='Matplotlib',comment='10 story building')
writer = FFMpegWriter(fps=5, metadata=metadata)
fig = plt.figure()

with writer.saving(fig, "Boston_SF_dzcompare.mp4", dpi = 200):

    time = np.linspace(0,100,num = 101)
    U = np.array([0,100, 100, 100, 100, 100])

    dzdt_SF = []
    dzdt_bos = []

    for t in range(int(t_final/dt)):
        Unew = np.copy(U)
        Unew1 = np.copy(U)

        for i in range(len(U)-1):
            U[0] = 0 
            U[-1] = U[-3]
            Unew[i] = U[i]+ b_bos*(U[i+1]-2*U[i]+U[i-1])
            U = Unew
            Uavg = np.average(U[0:5])
            consol_percent = (100-Uavg)/100
            dz_bos = consol_percent*dzmax_bos
        
        for i in range(len(U)-1):
            U[0] = 0 
            U[-1] = U[-3]
            Unew1[i] =  U[i]+ b_SF*(U[i+1]-2*U[i]+U[i-1])
            U = Unew1
            Uavg1 = np.average(Unew1[0:5])
            consol_percent1 = (100-Uavg1)/100
            dz_SF = consol_percent1*dzmax_SF


        if t%1 == 0:
            #plt.clf()
            if t == 0:
                plt.scatter(0,0, label = "Boston Max Consol", color = "cyan", marker = 'x')
                plt.scatter(0,0, label = "SF Max Consol", color = "orange", marker = 'x')            
                plt.legend()

            else:
                plt.scatter(t+1, dz_bos, label = "Boston Max Consol", color = "cyan",marker = 'x') #'r-', label = 'Boston Max Consol')
                plt.scatter(t+1, dz_SF, label = "SF Max Consol", color = "orange", marker = 'x' ) #, 'b-', label = 'SF Max Consol')
            plt.title("Consolidation vs time")
            plt.xlabel("Time (years)")
            plt.ylabel("Maximum Column Consolidation (m)")
            plt.xlim(0,100)
            plt.ylim(0,2)    
            
            writer.grab_frame()

            
        